In [27]:
import pandas as pd
import math

# Read the CSV file
df = pd.read_csv("restaurant.csv", header=0)
df = df[df[' industry_anzsic4_description'] == 'Cafes and Restaurants']
df = df[[' clue_small_area']]
df[' clue_small_area'] = df[' clue_small_area'].apply(lambda x: x.lower().split('(')[0])
df

clue_small_area
0             carlton
2          melbourne 
3          melbourne 
5          melbourne 
6           southbank
...               ...
3558       melbourne 
3559       melbourne 
3560  north melbourne
3561        docklands
3562        docklands

[2687 rows x 1 columns]

In [8]:
# df.to_csv('restaurant_filter.csv')

In [28]:
df = df.groupby(' clue_small_area').size().reset_index(name='counts')
df

clue_small_area  counts
0           carlton     320
1         docklands     292
2    east melbourne      65
3        kensington      48
4        melbourne     1517
5   north melbourne     102
6         parkville      52
7    port melbourne      29
8       south yarra      16
9         southbank     197
10  west melbourne       49

In [33]:
import json

ssa_code = open('../vic_sal/geo_vic_filter_ssa.geojson')
ssa_code_json = json.load(ssa_code)
ssa_code_json

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'coordinates': [[[146.00107417800007, -38.322139463999974],
      [146.00769698700003, -38.32289898399994],
      [146.008504957, -38.320923963999974],
      [146.0116878560001, -38.31941893399994],
      [146.0099993770001, -38.31675500399996],
      [146.00931926700002, -38.314441063999936],
      [146.01173771700007, -38.31258824399998],
      [146.01202471700003, -38.31147147399997],
      [146.01953185600007, -38.312339774999934],
      [146.019665335, -38.31482883499996],
      [146.03398195300005, -38.31668531599996],
      [146.03921915500007, -38.288894665999976],
      [146.03285840600006, -38.28813443599995],
      [146.03443027700004, -38.28151603599997],
      [146.03625571700002, -38.28096590599995],
      [146.03877965700008, -38.275659865999955],
      [146.03673269700005, -38.27450884599995],
      [146.0345316480001, -38.27067997599994],
      [146.03651559800005, -38.26853393599998],
    

In [34]:
ssa_code_json = ssa_code_json['features']
ssa_code_json

[{'type': 'Feature',
  'geometry': {'coordinates': [[[146.00107417800007, -38.322139463999974],
     [146.00769698700003, -38.32289898399994],
     [146.008504957, -38.320923963999974],
     [146.0116878560001, -38.31941893399994],
     [146.0099993770001, -38.31675500399996],
     [146.00931926700002, -38.314441063999936],
     [146.01173771700007, -38.31258824399998],
     [146.01202471700003, -38.31147147399997],
     [146.01953185600007, -38.312339774999934],
     [146.019665335, -38.31482883499996],
     [146.03398195300005, -38.31668531599996],
     [146.03921915500007, -38.288894665999976],
     [146.03285840600006, -38.28813443599995],
     [146.03443027700004, -38.28151603599997],
     [146.03625571700002, -38.28096590599995],
     [146.03877965700008, -38.275659865999955],
     [146.03673269700005, -38.27450884599995],
     [146.0345316480001, -38.27067997599994],
     [146.03651559800005, -38.26853393599998],
     [146.03488481800002, -38.26672691599998],
     [146.033226659

In [47]:
restaurant_geojson = {'type':'FeatureCollection','features':[]}

for index, data in df.iterrows():
    name = data[' clue_small_area']

    matchData = next((item for item in ssa_code_json if name in item["properties"]['name']),None)
    if(matchData != None):
        resultFeature = {'type':'Feature','geometry':matchData['geometry'],'properties': matchData['properties']}
        resultFeature['properties']['restaurant_number'] = data['counts']
    restaurant_geojson['features'].append(resultFeature)

restaurant_geojson

with open('restaurant_geojson.geojson', 'w') as fp:
    json.dump(restaurant_geojson, fp)
    